In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib.collections import LineCollection

import json
import numpy as np
import scipy as sp
import scipy.stats as st
import scipy.integrate as integrate
import sklearn
from sklearn import linear_model, decomposition

# import tikzplotlib

sns.set_style("whitegrid")
# sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (20,10)
legend_fontsize = 16
plt.rcParams.update({'font.size': 16})
from matplotlib import rc
rc('figure', **{'dpi' : 200})


## Алгоритм Метрополиса-Гастингса

In [ ]:
# Точки -- это двумерные массивы x
def q_sample(x, sigma=0.1):
    return x + np.random.normal(0, sigma, 2)

# Проверяем, будем ли принимать точку с новым логарифмом правдоподобия
def metropolis_hastings_log_accept(l, l_new):
    if l_new>l:
        return True
    else:
        return (np.random.rand() < (np.exp(l_new-l)))

def metropolis_hastings(func_log_likelihood, iterations, q_sigma=0.1, init_x=np.array([0, 0])):
    cur_x = init_x
    cur_l = func_log_likelihood(cur_x)
    samples, accept_bit = [cur_x], [1]
    for i in range(iterations):
        new_x = q_sample(cur_x, sigma=q_sigma)
        new_l = func_log_likelihood(new_x)
        samples.append(new_x)
        if (metropolis_hastings_log_accept(cur_l, new_l)):
            cur_x, cur_l = new_x, new_l
            accept_bit.append(1)
        else:
            accept_bit.append(0)
    return np.array(samples), np.array(accept_bit)

In [ ]:
alpha, mu_1, Sigma_1, mu_2, Sigma_2 = 2/3., np.array([3, 5]), .6*np.array([[2, -1], [-1, 1]]), np.array([-2, 2]), .6*np.array([[.5, 0.5], [0.5, 1.5]])

num_samples = 1000
data_firstcomponent = np.array( np.random.rand(num_samples) < alpha )
data_sample = np.zeros(shape=(num_samples, 2))
data_sample[ data_firstcomponent ] = np.random.multivariate_normal(mu_1, Sigma_1, sum(data_firstcomponent))
data_sample[ np.invert(data_firstcomponent) ] = np.random.multivariate_normal(mu_2, Sigma_2, sum(np.invert(data_firstcomponent)))

fig = plt.figure(figsize=(20,10))
ax = fig.subplots()
ax.scatter(data_sample[:,0], data_sample[:,1], s=15)
ax.set_xlim((-4, 7))
ax.set_ylim((-2, 8))
# plt.savefig("sample_mh0s.pdf", bbox_inches='tight')

In [ ]:
def gaussian_mixture_logpdf(x, alpha, mu1, Sigma1, mu2, Sigma2):
    return np.log(alpha * sp.stats.multivariate_normal.pdf(x, mean=mu1, cov=Sigma1) +
                  (1-alpha) * sp.stats.multivariate_normal.pdf(x, mean=mu2, cov=Sigma2))

def get_last_accept(samples, accept_bit):
    last_accept, last_bit = [], 0
    for i in range(len(samples)-1):
        last_accept.append(last_bit)
        if accept_bit[i] == 1:
            last_bit = i
    return last_accept

def plot_mh_walk(samples, last_accept, star_points=None, xlim=(-5,5), ylim=(-5,5), filename=None, texfile=None, figsize=(20, 10)):
    fig = plt.figure(figsize=figsize)
    ax = fig.subplots()
    coll = LineCollection(np.array([[samples[last_accept[i-1]], samples[i]] for i in range(1, len(samples))]),
                colors=np.array([palette[0] if x == 1 else '.9' for x in accept_bit[1:]]), zorder=10)
    ax.add_collection(coll)
    ax.autoscale_view()
    if star_points is not None:
        ax.scatter( [x[0] for x in star_points], [x[1] for x in star_points], marker='*', s=300, color='g', zorder=20 )

    ax.set_xlim(xlim)
    ax.set_ylim(ylim)
    
    if texfile is not None:
        tikzplotlib.save(texfile, axis_height='\\myplotheight', axis_width='\\myplotwidth')
    
    if filename is not None:
        plt.savefig(filename, bbox_inches='tight')
    
#     plt.show()

In [ ]:
num_samples = 1000
samples, accept_bit = metropolis_hastings(
    lambda x : gaussian_mixture_logpdf(x, alpha, mu_1, Sigma_1, mu_2, Sigma_2),
    num_samples, init_x=np.array([0,0]), q_sigma=.4)

last_accept = get_last_accept(samples, accept_bit)
# accepted_samples, rejected_samples = samples[np.where(accept_bit == 1)], samples[np.where(accept_bit == 0)]
# last_accept = get_last_accept(samples, accept_bit)
print("Total: %d samples, accepted: %d samples" % (num_samples, sum(accept_bit)))
plot_mh_walk(samples, last_accept, star_points=[mu_1, mu_2], xlim=(-4, 6), ylim=(-2, 7) )
plt.scatter(data_sample[:,0], data_sample[:,1], s=15, color='orange', alpha=0.25)

In [ ]:
def my_plot_mixture(num_samples, filename, q_sigma=0.1, figsize=(20,10)):
    samples, accept_bit = metropolis_hastings(
        lambda x : gaussian_mixture_logpdf(x, alpha, mu_1, Sigma_1, mu_2, Sigma_2),
        num_samples, init_x=np.array([0,0]), q_sigma=q_sigma)
    accepted_samples, rejected_samples = samples[np.where(accept_bit == 1)], samples[np.where(accept_bit == 0)]
    last_accept = get_last_accept(samples, accept_bit)
    plot_mh_walk(samples, last_accept, star_points=[mu_1, mu_2], xlim=(-4, 7), ylim=(-2, 8), filename=filename, figsize=figsize )

In [ ]:
my_plot_mixture(1500, None, figsize=(20,10), q_sigma=0.5)

## Пример реального обучения

In [ ]:
true_mu, true_Sigma = np.array([1, 3]), np.array([[4, -2], [-2, 2]])
data_points = np.random.multivariate_normal(true_mu, true_Sigma, 10000)
plt.scatter(data_points[:,0], data_points[:,1], s=5)

In [ ]:
data_sample = data_points[np.random.randint(0, 10000, 500)]
plt.scatter(data_sample[:,0], data_sample[:,1], s=5)

# tikzplotlib.save("sample_mh_sample.tex", axis_height='\\myplotheight', axis_width='\\myplotwidth')
# plt.show()

In [ ]:
fig = plt.figure(figsize=(20,10))
ax = fig.add_subplot(1,2,1)
ax.hist( data_sample[:,0],bins=20)
ax.set_xlabel("Значение X")
ax.set_ylabel("Частота")
ax = fig.add_subplot(1,2,2)
ax.hist( data_sample[:,1],bins=20)
ax.set_xlabel("Значение Y")
ax.set_ylabel("Частота")

# tikzplotlib.save("sample_mh_histogram.tex", axis_height='\\myplotheight', axis_width='.48\\myplotwidth')
# plt.show()

In [ ]:
def normal_log_likelihood(mu, Sigma):
    return np.sum(sp.stats.multivariate_normal.logpdf(data_sample, mean=mu, cov=Sigma))

samples, accept_bit = metropolis_hastings(
    lambda x : normal_log_likelihood(x, true_Sigma),
    300, init_x=np.array([0,0]))
accepted_samples, rejected_samples = samples[np.where(accept_bit == 1)], samples[np.where(accept_bit == 0)]

In [ ]:
normal_log_likelihood(np.array([0,0]), true_Sigma)

In [ ]:
print(samples[:100])
print(accept_bit[:100])

In [ ]:
data_sample = data_points[np.random.randint(0, 10000, 1000)]
num_samples = 3000
samples, accept_bit = metropolis_hastings(
    lambda x : normal_log_likelihood(x, true_Sigma),
    num_samples, init_x=np.array([0,0]), q_sigma=.05)

last_accept = get_last_accept(samples, accept_bit)
accepted_samples, rejected_samples = samples[np.where(accept_bit == 1)], samples[np.where(accept_bit == 0)]
# last_accept = get_last_accept(samples, accept_bit)
print("Total: %d samples, accepted: %d samples" % (num_samples, sum(accept_bit)))
plot_mh_walk(samples, last_accept, star_points=[true_mu], xlim=(0, 2), ylim=(2,4) )
# plt.scatter(data_sample[:,0], data_sample[:,1], s=65, color='orange', alpha=0.9)


In [ ]:
n, n_burn_in = 50, 50
samples_movingaverage = np.apply_along_axis( lambda x : np.convolve(x, np.ones((n,))/n, mode='valid'), axis=0, arr=accepted_samples)

In [ ]:
samples_movingaverage.shape

In [ ]:
fig = plt.figure(figsize=(20,10))
ax1 = fig.add_subplot(1,2,1)
ax1.hlines(1, 0, len(accepted_samples), color='orange', linestyle='dashed')
ax1.plot(accepted_samples[:, 0])
ax1.plot(np.arange(n/2, len(accepted_samples)-n/2+1), samples_movingaverage[:,0], color='g')
ax1.set_xlim((0, len(accepted_samples)))

ax2 = fig.add_subplot(1,2,2)
ax2.hlines(3, 0, len(accepted_samples), color='orange', linestyle='dashed')
ax2.plot(accepted_samples[:, 1])
ax2.plot(np.arange(n/2, len(accepted_samples)-n/2+1), samples_movingaverage[:,1], color='g')
ax2.set_xlim((0, len(accepted_samples)))

# tikzplotlib.save("sample_mh_ma.tex", axis_height='\\myplotheight', axis_width='.48\\myplotwidth')